In [1]:
import json
import glob
import os
import pandas as pd
import numpy as np
from skimage.external import tifffile
from IPython.display import clear_output
import itertools
import math

In [31]:
def mkdirp(directory):
    if not os.path.exists(directory):
        os.makedirs(directory)

In [32]:
def read_glomeruli_stats(run_dir, sample):
    if "misaxx" in run_dir:
        json_file = run_dir + "/output-docker/attachments/exported/" + sample + "/quantified/quantified.json.json" 
        json_data = None
        with open(json_file, "r") as f:
            json_data = json.load(f)
        tissue_json_file = run_dir + "/output-docker/attachments/exported/" + sample + "/tissue/quantified/quantified.json.json" 
        tissue_json_data = None
        with open(tissue_json_file, "r") as f:
            tissue_json_data = json.load(f)
        return { "num-glomeruli": json_data["misa-kidney-glomeruli:attachments/glomeruli"]["valid-glomeruli-number"], 
                "avg-diameter": json_data["misa-kidney-glomeruli:attachments/glomeruli"]["valid-glomeruli-diameter-average"], 
                "var-diameter": json_data["misa-kidney-glomeruli:attachments/glomeruli"]["valid-glomeruli-diameter-variance"], 
                "tissue-volume": tissue_json_data["misa-tissue:attachments/tissue"]["volume"]["value"] }
    else:
        json_file = run_dir + "/output/" + sample + "/glomeruli.json" 
        json_data = None
        with open(json_file, "r") as f:
            json_data = json.load(f)
        tissue_json_file = run_dir + "/output/" + sample + "/tissue.json"  if "python" in run_dir else run_dir + "/output/" + sample + "/tissue_quantified.json"
        tissue_json_data = None
        with open(tissue_json_file, "r") as f:
            tissue_json_data = json.load(f)
        return { "num-glomeruli": json_data["valid-glomeruli-number"], 
                "avg-diameter": json_data["valid-glomeruli-diameter-average"], 
                "var-diameter": json_data["valid-glomeruli-diameter-variance"], 
                "tissue-volume": tissue_json_data["volume-microns3"] }

In [33]:
samples = [os.path.basename(x) for x in glob.glob("glomeruli_python_snakemake_dag30_opMT/output/*") if os.path.isdir(x)]

glomeruli_stats = {}
for run_path in glob.glob("./glomeruli_*"):
    if not os.path.isdir(run_path):
        continue
    run = os.path.basename(run_path)
    glomeruli_stats[run] = {}
    
for run_path in glob.glob("./glomeruli_*"):
    if not os.path.isdir(run_path):
        continue
    run = os.path.basename(run_path)
    clear_output()
    for sample in samples:        
        print(run, sample)
        glomeruli_stats[run][sample] = read_glomeruli_stats(run_path, sample)

glomeruli_python_snakemake_dag30_noopMT Kontrolle_Ly6G M11a zoom08 z5 al647_14-26-05
glomeruli_python_snakemake_dag30_noopMT Kontrolle_Bonn 2a zoom063 z5 647_11-53-22
glomeruli_python_snakemake_dag30_noopMT d7 NTN 2b zoom063 z5_13-56-41
glomeruli_python_snakemake_dag30_noopMT Kontrolle_Ly6G M1a zoom08 z5 al647_12-38-06
glomeruli_python_snakemake_dag30_noopMT d15 NTN3a zoom08_16-04-45
glomeruli_python_snakemake_dag30_noopMT d7 NTN 3a zoom063 z5_17-01-52
glomeruli_python_snakemake_dag30_noopMT Kontrolle_Bonn 1a zoom063 z5 647_12-39-10
glomeruli_python_snakemake_dag30_noopMT d7 NTN 1a zoom063 z5 647_09-40-46
glomeruli_python_snakemake_dag30_noopMT Kontrolle_Bonn 2b_10-23-40
glomeruli_python_snakemake_dag30_noopMT d15 NTN 2a zoom08_15-33-00
glomeruli_python_snakemake_dag30_noopMT d15 NTN1a zoom08_15-19-34
glomeruli_python_snakemake_dag30_noopMT Kontrolle_Bonn 1b zoom063 z5 647_13-22-21
glomeruli_python_snakemake_dag30_noopMT d7 NTN2a neu_09-51-56
glomeruli_python_snakemake_dag30_noopMT d7 

In [34]:
df = pd.DataFrame()


qdatatypes = ["num-glomeruli", "tissue-volume"] #  "avg-diameter", "var-diameter" are broken in Python snakemake (at least in current results)
mkdirp("analysis/glomeruli/")

for qdatatype in qdatatypes:
    
    df = pd.DataFrame()
    
    for sample in samples:
        
        sample_data = {}
        for run in glomeruli_stats.keys():
            sample_data[run] = glomeruli_stats[run][sample][qdatatype]
                    
        sample_df = pd.DataFrame(data=sample_data, index=[sample])
        df = df.append(sample_df)
        
    df.to_csv("analysis/glomeruli/" + qdatatype + ".csv")
    
        

# Runtimes

In [3]:
def read_python_runtime(directory):
    with open(directory + "/runtime.log", "r") as f:
        return float(f.read()) / 60
    
def read_java_runtime(directory):
    with open(directory + "/output/runtime.log", "r") as f:
        return float(f.read()) / 1000 / 60
    
def read_misaxx_runtime(directory):
    json_data = None
    with open(directory + "/output-docker/runtime-log.json", "r") as f:
        json_data = json.load(f)
    thread0_data = json_data["entries"]["thread0"]
    end_times = [x["end-time"] for x in thread0_data]
    return np.max(end_times) / 1000 / 60

In [4]:
runtime_runs = []
runtime_runtimes = []

for run_path in glob.glob("./glomeruli_python*"):
    if not os.path.isdir(run_path):
        continue
    run = os.path.basename(run_path)
    rt = read_python_runtime(run_path)
    runtime_runs.append(run)
    runtime_runtimes.append(rt)
    
for run_path in glob.glob("./glomeruli_java*"):
    if not os.path.isdir(run_path):
        continue
    run = os.path.basename(run_path)
    rt = read_java_runtime(run_path)
    runtime_runs.append(run)
    runtime_runtimes.append(rt)  
    
for run_path in glob.glob("./glomeruli_cxx*"):
    if not os.path.isdir(run_path):
        continue
    run = os.path.basename(run_path)
    rt = read_misaxx_runtime(run_path)
    runtime_runs.append(run)
    runtime_runtimes.append(rt)

df_runtime = pd.DataFrame({"Runtime (min)": runtime_runtimes}, index=runtime_runs)

In [5]:
df_runtime

Runtime (min)
glomeruli_python_snakemake_dag30_opMT       888.783333
glomeruli_python_snakemake_dag30_noopMT     926.216667
glomeruli_java_imglib2_dag30_noopMT        5510.610133
glomeruli_cxx_misaxx_dag30_noopMT            40.441508
glomeruli_cxx_misaxx_noMT_optMT             334.215405
glomeruli_cxx_misaxx_noMT_nooptMT           335.579139
glomeruli_cxx_misaxx_dag30_opMT              41.109999

In [6]:
mkdirp("analysis/glomeruli")
df_runtime.to_csv("analysis/glomeruli/runtimes.csv")

# Intra-implementation equality

In [49]:
qdatatypes = ["num-glomeruli", "avg-diameter", "var-diameter", "tissue-volume"]

for qdatatype in qdatatypes:
    print(qdatatype)
    df = pd.read_csv("analysis/glomeruli/" + qdatatype + ".csv") 
    for implementation in ["cxx", "java", "python"]:
        columns = [x for x in df.columns if implementation in x]
        idf = df.filter(columns)
        for index, row in idf.iterrows():
            for pair in itertools.product(list(row), list(row)):
                assert math.isclose(*pair)

num-glomeruli
avg-diameter
var-diameter
tissue-volume


# Extract non-accumulated statistics

In [3]:
def read_glomeruli_unaccumulated_stats(run_dir, run, sample):
    if "misaxx" in run_dir:
        json_file = run_dir + "/output-docker/attachments/exported/" + sample + "/quantified/quantified.json.json" 
        json_data = None
        with open(json_file, "r") as f:
            json_data = json.load(f)
              
        json_data = json_data["misa-kidney-glomeruli:attachments/glomeruli"]["data"]
        
        column_run = []
        column_sample = []
        column_label = []
        column_diameter = []
        column_pixels = []
        column_volume = []
        
        for key, value in json_data.items():
            if not value["valid"]:
                continue
            column_run.append(run)
            column_sample.append(sample)
            column_label.append(value["label"])
            column_diameter.append(value["diameter"]["value"])
            column_pixels.append(value["pixels"]["count"])
            column_volume.append(value["volume"]["value"])
                   
        return pd.DataFrame({ "run": column_run,
                            "sample": column_sample,
                            "label": column_label,
                            "diameter": column_diameter,
                            "pixels": column_pixels,
                            "volume": column_volume}, index=list(range(len(column_run))))
    else:
        json_file = run_dir + "/output/" + sample + "/glomeruli.json" 
        json_data = None
        with open(json_file, "r") as f:
            json_data = json.load(f)
        json_data = json_data["data"]
        
        column_run = []
        column_sample = []
        column_label = []
        column_diameter = []
        column_pixels = []
        column_volume = []
        
        for key, value in json_data.items():
            if not value["valid"]:
                continue
            column_run.append(run)
            column_sample.append(sample)
            column_label.append(value["label"])
            column_diameter.append(value["diameter"])
            column_pixels.append(value["pixels"])
            column_volume.append(value["volume"])
                   
        return pd.DataFrame({ "run": column_run,
                            "sample": column_sample,
                            "label": column_label,
                            "diameter": column_diameter,
                            "pixels": column_pixels,
                            "volume": column_volume}, index=list(range(len(column_run))))

In [38]:
df = pd.DataFrame()
samples = [os.path.basename(x) for x in glob.glob("glomeruli_python_snakemake_dag30_opMT/output/*") if os.path.isdir(x)]

for run_path in ["glomeruli_cxx_misaxx_dag30_opMT", "glomeruli_java_imglib2_dag30_noopMT", "glomeruli_python_snakemake_dag30_opMT"]:
    if not os.path.isdir(run_path):
        continue
    run = os.path.basename(run_path)
    clear_output()
    for sample in samples:        
        print(run, sample)
        df = df.append(read_glomeruli_unaccumulated_stats(run_dir=run_path, run=run, sample=sample), ignore_index=True)

mkdirp("analysis/glomeruli")
df.to_csv("analysis/glomeruli/glomeruli_statistics.csv", index=False)
df_all_glomeruli = df

glomeruli_python_snakemake_dag30_opMT Kontrolle_Ly6G M11a zoom08 z5 al647_14-26-05
glomeruli_python_snakemake_dag30_opMT Kontrolle_Bonn 2a zoom063 z5 647_11-53-22
glomeruli_python_snakemake_dag30_opMT d7 NTN 2b zoom063 z5_13-56-41
glomeruli_python_snakemake_dag30_opMT Kontrolle_Ly6G M1a zoom08 z5 al647_12-38-06
glomeruli_python_snakemake_dag30_opMT d15 NTN3a zoom08_16-04-45
glomeruli_python_snakemake_dag30_opMT d7 NTN 3a zoom063 z5_17-01-52
glomeruli_python_snakemake_dag30_opMT Kontrolle_Bonn 1a zoom063 z5 647_12-39-10
glomeruli_python_snakemake_dag30_opMT d7 NTN 1a zoom063 z5 647_09-40-46
glomeruli_python_snakemake_dag30_opMT Kontrolle_Bonn 2b_10-23-40
glomeruli_python_snakemake_dag30_opMT d15 NTN 2a zoom08_15-33-00
glomeruli_python_snakemake_dag30_opMT d15 NTN1a zoom08_15-19-34
glomeruli_python_snakemake_dag30_opMT Kontrolle_Bonn 1b zoom063 z5 647_13-22-21
glomeruli_python_snakemake_dag30_opMT d7 NTN2a neu_09-51-56
glomeruli_python_snakemake_dag30_opMT d7 NTN 3b zoom063 z5 488- 647_1

# Generate accumulated statistics
* Reason is a bug in Python implementation generating wrong avg and var diameters
* Non-accumulated statistics are not affected

In [39]:
mkdirp("analysis/glomeruli/")
implementations = ["glomeruli_cxx_misaxx_dag30_opMT",
    "glomeruli_java_imglib2_dag30_noopMT",
    "glomeruli_python_snakemake_dag30_opMT"]
df = df_all_glomeruli

In [41]:
df_num_glomeruli = pd.DataFrame({ impl: [ np.count_nonzero((df["run"] == impl) & (df["sample"] == sample)) for sample in samples ] for impl in implementations }, index=samples)
df_num_glomeruli.to_csv("analysis/glomeruli/num-glomeruli.csv")
df_num_glomeruli

glomeruli_cxx_misaxx_dag30_opMT  \
Kontrolle_Ly6G M11a zoom08 z5 al647_14-26-05                            14579   
Kontrolle_Bonn 2a zoom063 z5 647_11-53-22                               15328   
d7 NTN 2b zoom063 z5_13-56-41                                           11938   
Kontrolle_Ly6G M1a zoom08 z5 al647_12-38-06                             13981   
d15 NTN3a zoom08_16-04-45                                                4581   
d7 NTN 3a zoom063 z5_17-01-52                                           17111   
Kontrolle_Bonn 1a zoom063 z5 647_12-39-10                               14234   
d7 NTN 1a zoom063 z5 647_09-40-46                                       17196   
Kontrolle_Bonn 2b_10-23-40                                              13253   
d15 NTN 2a zoom08_15-33-00                                              10674   
d15 NTN1a zoom08_15-19-34                                                9300   
Kontrolle_Bonn 1b zoom063 z5 647_13-22-21                               13770   
d7 NTN2a neu_09-51-56                                                   14119   
d7 NTN 3b zoom063 z5 488- 647_12-11-22                                  15141   
Kontrolle_Ly6G M11b zoom08 z5 al647_13-43-00                            14234   
d7 NTN 2a zoom063 z5 488-647_15-46-09                                   13599   
d15 NTN1b zoom08_13-43-09                                               11725   
d7 NTN 1b zoom063 z5 647_10-51-03                                       16678   
Kontrolle_Ly6G M9a zoom08 z5 al647_11-36-12                             13167   
Kontrolle_Ly6G M9b zoom08 z5 al647_12-10-14                              9583   
d15 NTN2b zoom08_14-23-01                                               10771   
d15 NTN3b zoom08_16-29-01                                               11557   
Kontrolle_Ly6G M1b zoom08 z5 al647_13-05-34                             16597   

                                              glomeruli_java_imglib2_dag30_noopMT  \
Kontrolle_Ly6G M11a zoom08 z5 al647_14-26-05                                14547   
Kontrolle_Bonn 2a zoom063 z5 647_11-53-22                                   15330   
d7 NTN 2b zoom063 z5_13-56-41                                               12012   
Kontrolle_Ly6G M1a zoom08 z5 al647_12-38-06                                 14355   
d15 NTN3a zoom08_16-04-45                                                    4852   
d7 NTN 3a zoom063 z5_17-01-52                                               17153   
Kontrolle_Bonn 1a zoom063 z5 647_12-39-10                                   14165   
d7 NTN 1a zoom063 z5 647_09-40-46                                           17156   
Kontrolle_Bonn 2b_10-23-40                                                  13245   
d15 NTN 2a zoom08_15-33-00                                                  10670   
d15 NTN1a zoom08_15-19-34                                                    9285   
Kontrolle_Bonn 1b zoom063 z5 647_13-22-21                                   13748   
d7 NTN2a neu_09-51-56                                                       14050   
d7 NTN 3b zoom063 z5 488- 647_12-11-22                                      15164   
Kontrolle_Ly6G M11b zoom08 z5 al647_13-43-00                                14241   
d7 NTN 2a zoom063 z5 488-647_15-46-09                                       13566   
d15 NTN1b zoom08_13-43-09                                                   11692   
d7 NTN 1b zoom063 z5 647_10-51-03                                           16647   
Kontrolle_Ly6G M9a zoom08 z5 al647_11-36-12                                 13225   
Kontrolle_Ly6G M9b zoom08 z5 al647_12-10-14                                  9623   
d15 NTN2b zoom08_14-23-01                                                   10601   
d15 NTN3b zoom08_16-29-01                                                   11517   
Kontrolle_Ly6G M1b zoom08 z5 al647_13-05-34                                 16662   

                                              glomeruli_pyth

In [42]:
df_avg_diameter = pd.DataFrame({ impl: [ np.mean(df.loc[(df["run"] == impl) & (df["sample"] == sample), "diameter"]) for sample in samples ] for impl in implementations }, index=samples)
df_avg_diameter.to_csv("analysis/glomeruli/avg-diameter.csv")
df_avg_diameter

glomeruli_cxx_misaxx_dag30_opMT  \
Kontrolle_Ly6G M11a zoom08 z5 al647_14-26-05                        53.467185   
Kontrolle_Bonn 2a zoom063 z5 647_11-53-22                           55.843212   
d7 NTN 2b zoom063 z5_13-56-41                                       57.153322   
Kontrolle_Ly6G M1a zoom08 z5 al647_12-38-06                         52.892893   
d15 NTN3a zoom08_16-04-45                                           56.707024   
d7 NTN 3a zoom063 z5_17-01-52                                       68.749191   
Kontrolle_Bonn 1a zoom063 z5 647_12-39-10                           58.689717   
d7 NTN 1a zoom063 z5 647_09-40-46                                   61.386247   
Kontrolle_Bonn 2b_10-23-40                                          67.392109   
d15 NTN 2a zoom08_15-33-00                                          62.766302   
d15 NTN1a zoom08_15-19-34                                           57.493706   
Kontrolle_Bonn 1b zoom063 z5 647_13-22-21                           58.534477   
d7 NTN2a neu_09-51-56                                               66.033293   
d7 NTN 3b zoom063 z5 488- 647_12-11-22                              66.268211   
Kontrolle_Ly6G M11b zoom08 z5 al647_13-43-00                        55.095458   
d7 NTN 2a zoom063 z5 488-647_15-46-09                               67.105203   
d15 NTN1b zoom08_13-43-09                                           62.467674   
d7 NTN 1b zoom063 z5 647_10-51-03                                   62.540799   
Kontrolle_Ly6G M9a zoom08 z5 al647_11-36-12                         53.635118   
Kontrolle_Ly6G M9b zoom08 z5 al647_12-10-14                         50.266897   
d15 NTN2b zoom08_14-23-01                                           59.945751   
d15 NTN3b zoom08_16-29-01                                           57.809484   
Kontrolle_Ly6G M1b zoom08 z5 al647_13-05-34                         51.998772   

                                              glomeruli_java_imglib2_dag30_noopMT  \
Kontrolle_Ly6G M11a zoom08 z5 al647_14-26-05                            53.544137   
Kontrolle_Bonn 2a zoom063 z5 647_11-53-22                               56.019465   
d7 NTN 2b zoom063 z5_13-56-41                                           57.200416   
Kontrolle_Ly6G M1a zoom08 z5 al647_12-38-06                             52.511437   
d15 NTN3a zoom08_16-04-45                                               56.005516   
d7 NTN 3a zoom063 z5_17-01-52                                           68.925616   
Kontrolle_Bonn 1a zoom063 z5 647_12-39-10                               58.897564   
d7 NTN 1a zoom063 z5 647_09-40-46                                       61.206324   
Kontrolle_Bonn 2b_10-23-40                                              67.534248   
d15 NTN 2a zoom08_15-33-00                                              63.120989   
d15 NTN1a zoom08_15-19-34                                               57.615509   
Kontrolle_Bonn 1b zoom063 z5 647_13-22-21                               58.774761   
d7 NTN2a neu_09-51-56                                                   66.368662   
d7 NTN 3b zoom063 z5 488- 647_12-11-22                                  66.435016   
Kontrolle_Ly6G M11b zoom08 z5 al647_13-43-00                            55.263874   
d7 NTN 2a zoom063 z5 488-647_15-46-09                                   67.269119   
d15 NTN1b zoom08_13-43-09                                               62.375772   
d7 NTN 1b zoom063 z5 647_10-51-03                                       62.646400   
Kontrolle_Ly6G M9a zoom08 z5 al647_11-36-12                             53.441393   
Kontrolle_Ly6G M9b zoom08 z5 al647_12-10-14                             50.315749   
d15 NTN2b zoom08_14-23-01                                               60.340434   
d15 NTN3b zoom08_16-29-01                                               58.004938   
Kontrolle_Ly6G M1b zoom08 z5 al647_13-05-34                             52.130099   

                                              glomeruli_pyth

In [43]:
df_var_diameter = pd.DataFrame({ impl: [ np.var(df.loc[(df["run"] == impl) & (df["sample"] == sample), "diameter"]) for sample in samples ] for impl in implementations }, index=samples)
df_var_diameter.to_csv("analysis/glomeruli/var-diameter.csv")
df_var_diameter

glomeruli_cxx_misaxx_dag30_opMT  \
Kontrolle_Ly6G M11a zoom08 z5 al647_14-26-05                       104.864367   
Kontrolle_Bonn 2a zoom063 z5 647_11-53-22                          124.062453   
d7 NTN 2b zoom063 z5_13-56-41                                      176.754352   
Kontrolle_Ly6G M1a zoom08 z5 al647_12-38-06                        115.634121   
d15 NTN3a zoom08_16-04-45                                          270.323284   
d7 NTN 3a zoom063 z5_17-01-52                                      229.756503   
Kontrolle_Bonn 1a zoom063 z5 647_12-39-10                          112.037312   
d7 NTN 1a zoom063 z5 647_09-40-46                                  267.296529   
Kontrolle_Bonn 2b_10-23-40                                         245.709768   
d15 NTN 2a zoom08_15-33-00                                         278.057932   
d15 NTN1a zoom08_15-19-34                                          203.364704   
Kontrolle_Bonn 1b zoom063 z5 647_13-22-21                          167.791046   
d7 NTN2a neu_09-51-56                                              277.746996   
d7 NTN 3b zoom063 z5 488- 647_12-11-22                             217.498845   
Kontrolle_Ly6G M11b zoom08 z5 al647_13-43-00                       116.537370   
d7 NTN 2a zoom063 z5 488-647_15-46-09                              389.852285   
d15 NTN1b zoom08_13-43-09                                          415.401328   
d7 NTN 1b zoom063 z5 647_10-51-03                                  264.692142   
Kontrolle_Ly6G M9a zoom08 z5 al647_11-36-12                        159.818943   
Kontrolle_Ly6G M9b zoom08 z5 al647_12-10-14                        108.029237   
d15 NTN2b zoom08_14-23-01                                          333.720924   
d15 NTN3b zoom08_16-29-01                                          211.917441   
Kontrolle_Ly6G M1b zoom08 z5 al647_13-05-34                         99.724788   

                                              glomeruli_java_imglib2_dag30_noopMT  \
Kontrolle_Ly6G M11a zoom08 z5 al647_14-26-05                           102.732692   
Kontrolle_Bonn 2a zoom063 z5 647_11-53-22                              123.349880   
d7 NTN 2b zoom063 z5_13-56-41                                          175.375584   
Kontrolle_Ly6G M1a zoom08 z5 al647_12-38-06                            118.256008   
d15 NTN3a zoom08_16-04-45                                              276.816995   
d7 NTN 3a zoom063 z5_17-01-52                                          230.324583   
Kontrolle_Bonn 1a zoom063 z5 647_12-39-10                              108.576235   
d7 NTN 1a zoom063 z5 647_09-40-46                                      264.881453   
Kontrolle_Bonn 2b_10-23-40                                             244.506661   
d15 NTN 2a zoom08_15-33-00                                             276.631574   
d15 NTN1a zoom08_15-19-34                                              200.487768   
Kontrolle_Bonn 1b zoom063 z5 647_13-22-21                              166.052617   
d7 NTN2a neu_09-51-56                                                  273.366786   
d7 NTN 3b zoom063 z5 488- 647_12-11-22                                 216.992687   
Kontrolle_Ly6G M11b zoom08 z5 al647_13-43-00                           115.544285   
d7 NTN 2a zoom063 z5 488-647_15-46-09                                  388.627411   
d15 NTN1b zoom08_13-43-09                                              413.035363   
d7 NTN 1b zoom063 z5 647_10-51-03                                      260.566335   
Kontrolle_Ly6G M9a zoom08 z5 al647_11-36-12                            148.802063   
Kontrolle_Ly6G M9b zoom08 z5 al647_12-10-14                            107.103100   
d15 NTN2b zoom08_14-23-01                                              331.536174   
d15 NTN3b zoom08_16-29-01                                              206.306471   
Kontrolle_Ly6G M1b zoom08 z5 al647_13-05-34                            100.143018   

                                              glomeruli_pyth